In [1]:
from sqlalchemy import create_engine, text
import pandas as pd

# Database connection setup
DATABASE_TYPE = 'mysql'
DBAPI = 'mysqlconnector'
HOST = 'fashionretail.c3q4cw8i0vbc.us-east-2.rds.amazonaws.com'
USER = 'admin'
PASSWORD = 'bsan-6080-project'
DATABASE = 'fashion_retail'
DATABASE_URL = f"{DATABASE_TYPE}+{DBAPI}://{USER}:{PASSWORD}@{HOST}/{DATABASE}"
engine = create_engine(DATABASE_URL, echo=True)

# Load the CSV file
csv_file_path = 'Fashion_Retail_Sales_Clean.csv'
df = pd.read_csv(csv_file_path)

# Convert 'Date Purchase' to datetime and 'Purchase Amount (USD)' to numeric
df['DatePurchased'] = pd.to_datetime(df['Date Purchase'])
df['Revenue'] = pd.to_numeric(df['Purchase Amount (USD)'], errors='coerce')

# Extract date parts
df['Day'] = df['DatePurchased'].dt.day
df['Month'] = df['DatePurchased'].dt.month
df['Quarter'] = df['DatePurchased'].dt.quarter
df['Year'] = df['DatePurchased'].dt.year

# Rename columns to match database schema
df = df.rename(columns={'Customer Reference ID': 'CustomerID', 'Item Purchased': 'ItemsPurchased'})

# SQL for creating tables
create_table_statements = [
    """
    CREATE TABLE IF NOT EXISTS fact_purchases (
        PurchaseID INT AUTO_INCREMENT PRIMARY KEY,
        DatePurchased DATE,
        ItemsPurchased VARCHAR(255),
        Revenue DECIMAL(10, 2)
    );
    """,
    """
    CREATE TABLE IF NOT EXISTS dim_date (
        DatePurchased DATE PRIMARY KEY,
        Day INT,
        Month INT,
        Quarter INT,
        Year INT
    );
    """,
    """
    CREATE TABLE IF NOT EXISTS fact_customer_purchases (
        CustomerID INT,
        DatePurchased DATE,
        ItemsPurchased VARCHAR(255),
        Revenue DECIMAL(10, 2),
        PRIMARY KEY (CustomerID, DatePurchased),
        FOREIGN KEY (DatePurchased) REFERENCES dim_date(DatePurchased)
    );
    """
]

# Insertion queries with ON DUPLICATE KEY UPDATE
queries = {
    'fact_purchases': """
    INSERT INTO fact_purchases (DatePurchased, ItemsPurchased, Revenue)
    VALUES (:DatePurchased, :ItemsPurchased, :Revenue)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    """,
    'dim_date': """
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (:DatePurchased, :Day, :Month, :Quarter, :Year)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    """,
    'fact_customer_purchases': """
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue)
    VALUES (:CustomerID, :DatePurchased, :ItemsPurchased, :Revenue)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    """
}

# Execute the table creation and data insertion within a single transaction
with engine.begin() as conn:
    # Ensure tables exist
    for statement in create_table_statements:
        conn.execute(text(statement))
    
    # Insert data into all tables
    for index, row in df.iterrows():
        row['DatePurchased'] = row['DatePurchased'].date().isoformat()  # Convert to ISO format string
        for table, query in queries.items():
            conn.execute(text(query), row.to_dict())

print("All tables populated successfully.")



2024-04-23 17:18:09,539 INFO sqlalchemy.engine.Engine SELECT DATABASE()
2024-04-23 17:18:09,542 INFO sqlalchemy.engine.Engine [raw sql] {}
2024-04-23 17:18:10,032 INFO sqlalchemy.engine.Engine SELECT @@sql_mode
2024-04-23 17:18:10,035 INFO sqlalchemy.engine.Engine [raw sql] {}
2024-04-23 17:18:10,281 INFO sqlalchemy.engine.Engine SELECT @@lower_case_table_names
2024-04-23 17:18:10,284 INFO sqlalchemy.engine.Engine [raw sql] {}
2024-04-23 17:18:10,447 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2024-04-23 17:18:10,614 INFO sqlalchemy.engine.Engine 
    CREATE TABLE IF NOT EXISTS fact_purchases (
        PurchaseID INT AUTO_INCREMENT PRIMARY KEY,
        DatePurchased DATE,
        ItemsPurchased VARCHAR(255),
        Revenue DECIMAL(10, 2)
    );
    
2024-04-23 17:18:10,618 INFO sqlalchemy.engine.Engine [generated in 0.16642s] {}
2024-04-23 17:18:10,911 INFO sqlalchemy.engine.Engine 
    CREATE TABLE IF NOT EXISTS dim_date (
        DatePurchased DATE PRIMARY KEY,
        Day INT,
 

2024-04-23 17:18:15,224 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    
2024-04-23 17:18:15,227 INFO sqlalchemy.engine.Engine [cached since 3.156s ago] {'CustomerID': 3997, 'DatePurchased': '2022-11-27', 'ItemsPurchased': 'Wallet', 'Revenue': 3003.0}
2024-04-23 17:18:15,468 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_purchases (DatePurchased, ItemsPurchased, Revenue)
    VALUES (%(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    
2024-04-23 17:18:15,471 INFO sqlalchemy.engine.Engine [cached since 4.146s ago] {'DatePurchased': '2022-12-11', 'ItemsPurchased': 'Onesie', 'Revenue': 2914.0}
2024-04-23 17:18:15,719 INFO sqlalchemy.e

2024-04-23 17:18:19,536 INFO sqlalchemy.engine.Engine [cached since 7.712s ago] {'DatePurchased': '2023-03-19', 'Day': 19, 'Month': 3, 'Quarter': 1, 'Year': 2023}
2024-04-23 17:18:19,781 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    
2024-04-23 17:18:19,784 INFO sqlalchemy.engine.Engine [cached since 7.713s ago] {'CustomerID': 4108, 'DatePurchased': '2023-03-19', 'ItemsPurchased': 'Slippers', 'Revenue': 2356.0}
2024-04-23 17:18:20,028 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_purchases (DatePurchased, ItemsPurchased, Revenue)
    VALUES (%(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    
2024-04-23 17:18:20,031 INFO sqlalc

2024-04-23 17:18:24,084 INFO sqlalchemy.engine.Engine 
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (%(DatePurchased)s, %(Day)s, %(Month)s, %(Quarter)s, %(Year)s)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    
2024-04-23 17:18:24,087 INFO sqlalchemy.engine.Engine [cached since 12.26s ago] {'DatePurchased': '2023-07-17', 'Day': 17, 'Month': 7, 'Quarter': 3, 'Year': 2023}
2024-04-23 17:18:24,338 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    
2024-04-23 17:18:24,341 INFO sqlalchemy.engine.Engine [cached since 12.27s ago] {'CustomerID': 4017, 'DatePurchased': '2023-07-17', 'ItemsPurchased': 'Gloves', 'Revenue': 2895.0}
2024-04-23 17

2024-04-23 17:18:28,531 INFO sqlalchemy.engine.Engine [cached since 17.21s ago] {'DatePurchased': '2023-02-11', 'ItemsPurchased': 'Jeans', 'Revenue': 2814.0}
2024-04-23 17:18:28,780 INFO sqlalchemy.engine.Engine 
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (%(DatePurchased)s, %(Day)s, %(Month)s, %(Quarter)s, %(Year)s)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    
2024-04-23 17:18:28,783 INFO sqlalchemy.engine.Engine [cached since 16.96s ago] {'DatePurchased': '2023-02-11', 'Day': 11, 'Month': 2, 'Quarter': 1, 'Year': 2023}
2024-04-23 17:18:29,060 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    
2024-04-23 17:18:29,063 INFO sqlal

...

2024-04-23 18:13:29,955 INFO sqlalchemy.engine.Engine 
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (%(DatePurchased)s, %(Day)s, %(Month)s, %(Quarter)s, %(Year)s)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    
2024-04-23 18:13:29,957 INFO sqlalchemy.engine.Engine [cached since 2582s ago] {'DatePurchased': '2023-08-11', 'Day': 11, 'Month': 8, 'Quarter': 3, 'Year': 2023}
2024-04-23 18:13:30,237 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    
2024-04-23 18:13:30,240 INFO sqlalchemy.engine.Engine [cached since 2582s ago] {'CustomerID': 3973, 'DatePurchased': '2023-08-11', 'ItemsPurchased': 'Pajamas', 'Revenue': 33.0}
2024-04-23 18:13

2024-04-23 18:13:34,243 INFO sqlalchemy.engine.Engine [cached since 2587s ago] {'DatePurchased': '2023-08-25', 'ItemsPurchased': 'Jacket', 'Revenue': 110.0}
2024-04-23 18:13:34,492 INFO sqlalchemy.engine.Engine 
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (%(DatePurchased)s, %(Day)s, %(Month)s, %(Quarter)s, %(Year)s)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    
2024-04-23 18:13:34,495 INFO sqlalchemy.engine.Engine [cached since 2587s ago] {'DatePurchased': '2023-08-25', 'Day': 25, 'Month': 8, 'Quarter': 3, 'Year': 2023}
2024-04-23 18:13:34,741 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    
2024-04-23 18:13:34,743 INFO sqlalch

2024-04-23 18:13:38,760 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_purchases (DatePurchased, ItemsPurchased, Revenue)
    VALUES (%(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    
2024-04-23 18:13:38,763 INFO sqlalchemy.engine.Engine [cached since 2591s ago] {'DatePurchased': '2023-02-13', 'ItemsPurchased': 'Trench Coat', 'Revenue': 17.0}
2024-04-23 18:13:39,011 INFO sqlalchemy.engine.Engine 
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (%(DatePurchased)s, %(Day)s, %(Month)s, %(Quarter)s, %(Year)s)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    
2024-04-23 18:13:39,014 INFO sqlalchemy.engine.Engine [cached since 2591s ago] {'DatePurchased': '2023-02-13', 'Day': 13, 'Month': 2, 'Quarter': 1, 'Year': 2023}
2024-04-23 18:13:39,258 INFO sqlalchemy.engine.Engine 
    INSERT INT

2024-04-23 18:13:43,035 INFO sqlalchemy.engine.Engine [cached since 2595s ago] {'CustomerID': 4110, 'DatePurchased': '2022-10-15', 'ItemsPurchased': 'Polo Shirt', 'Revenue': 42.0}
2024-04-23 18:13:43,286 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_purchases (DatePurchased, ItemsPurchased, Revenue)
    VALUES (%(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    
2024-04-23 18:13:43,288 INFO sqlalchemy.engine.Engine [cached since 2596s ago] {'DatePurchased': '2023-01-20', 'ItemsPurchased': 'Tank Top', 'Revenue': 113.0}
2024-04-23 18:13:43,535 INFO sqlalchemy.engine.Engine 
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (%(DatePurchased)s, %(Day)s, %(Month)s, %(Quarter)s, %(Year)s)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    
2024-04-23 18:13:43,537 INFO sqlalchemy.engine.Engine

2024-04-23 18:13:47,558 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue);
    
2024-04-23 18:13:47,561 INFO sqlalchemy.engine.Engine [cached since 2599s ago] {'CustomerID': 4001, 'DatePurchased': '2023-03-22', 'ItemsPurchased': 'Backpack', 'Revenue': 115.0}
2024-04-23 18:13:47,647 INFO sqlalchemy.engine.Engine COMMIT
All tables populated successfully.
